** Найти компании которые упали меньше всего весной 2020

In [1]:
pip install pandas-datareader get-all-tickers 

Looking in indexes: https://pypi.org/simple, https://pypi.ngc.nvidia.com
Note: you may need to restart the kernel to use updated packages.


In [2]:
import pandas as pd
from pandas_datareader import data
pd.set_option('display.max_rows', None)

In [3]:
def get_tickers():
    import requests
    import pandas as pd

    headers = {
        'authority': 'api.nasdaq.com',
        'accept': 'application/json, text/plain, */*',
        'user-agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.141 Safari/537.36',
        'origin': 'https://www.nasdaq.com',
        'sec-fetch-site': 'same-site',
        'sec-fetch-mode': 'cors',
        'sec-fetch-dest': 'empty',
        'referer': 'https://www.nasdaq.com/',
        'accept-language': 'en-US,en;q=0.9',
    }

    params = (
        ('tableonly', 'true'),
        ('limit', '25'),
        ('offset', '0'),
        ('download', 'true'),
    )

    r = requests.get('https://api.nasdaq.com/api/screener/stocks', headers=headers, params=params)
    data = r.json()['data']
    df = pd.DataFrame(data['rows'], columns=data['headers'])
    df['market_cap'] = pd.to_numeric(df.marketCap) / 1_000_000_000
    df = df.set_index('symbol')
    return df 
all_tickers = get_tickers()
all_tickers

name    lastsale  \
symbol                                                                          
A                          Agilent Technologies Inc. Common Stock     $149.95   
AA                                Alcoa Corporation Common Stock       $38.27   
AAC             Ares Acquisition Corporation Class A Ordinary ...       $9.75   
AACG             ATA Creativity Global American Depositary Shares       $3.08   
AAIC                Arlington Asset Investment Corp Class A (new)       $3.91   
AAIC^B                     Arlington Asset Investment Corp 7.00%     $25.0027   
AAIC^C          Arlington Asset Investment Corp 8.250% Seies C...     $25.115   
AAIN            Arlington Asset Investment Corp 6.000% Senior ...      $24.80   
AAL                     American Airlines Group Inc. Common Stock      $21.46   
AAMC                         Altisource Asset Management Corp Com    $15.5034   
AAME                   Atlantic American Corporation Common Stock       $4.08   
AAN                    Aarons Holdings Company Inc. Common Stock       $30.13   
AAOI                    Applied Optoelectronics Inc. Common Stock       $7.21   
AAON                                       AAON Inc. Common Stock      $59.87   
AAP             Advance Auto Parts Inc Advance Auto Parts Inc W/I     $215.37   
AAPL                                      Apple Inc. Common Stock     $146.77   
AAQC            Accelerate Acquisition Corp. Class A Common Stock       $9.68   
AAT                       American Assets Trust Inc. Common Stock      $36.85   
AATC              Autoscope Technologies Corporation Common Stock     $6.3214   
AAU                           Almaden Minerals Ltd. Common Shares       $0.41   
AAWW                Atlas Air Worldwide Holdings NEW Common Stock      $65.98   
AB                          AllianceBernstein Holding L.P.  Units      $46.59   
ABB                                          ABB Ltd Common Stock      $36.83   
ABBV                                     AbbVie Inc. Common Stock     $117.96   
ABC                    AmerisourceBergen Corporation Common Stock     $121.41   
ABCB                                  Ameris Bancorp Common Stock      $47.33   
ABCL                       AbCellera Biologics Inc. Common Shares      $14.85   
ABCM                         Abcam plc American Depositary Shares      $18.01   
ABEO                        Abeona Therapeutics Inc. Common Stock       $1.25   
ABEV            Ambev S.A. American Depositary Shares (Each re...       $3.24   
ABG                      Asbury Automotive Group Inc Common Stock     $196.92   
ABGI              ABG Acquisition Corp. I Class A Ordinary Shares       $9.74   
ABIO                             ARCA biopharma Inc. Common Stock       $2.98   
ABM                      ABM Industries Incorporated Common Stock      $45.74   
ABMD                                    ABIOMED Inc. Common Stock     $321.96   
ABNB                             Airbnb Inc. Class A Common Stock     $141.58   
ABOS                     Acumen Pharmaceuticals Inc. Common Stock      $14.50   
ABR                               Arbor Realty Trust Common Stock      $17.94   
ABR^D           Arbor Realty Trust 6.375% Series D Cumulative ...      $25.54   
ABSI                               Absci Corporation Common Stock      $23.20   
ABST                   Absolute Software Corporation Common Stock      $13.66   
ABT                              Abbott Laboratories Common Stock     $119.81   
ABTX                      Allegiance Bancshares Inc. Common Stock      $35.55   
ABUS                   Arbutus Biopharma Corporation Common Stock       $2.70   
AC                     Associated Capital Group Inc. Common Stock      $37.77   
ACA                                     Arcosa Inc. Common Stock       $53.54   
ACAD                     ACADIA Pharmaceuticals Inc. Common Stock      $21.15   
ACAH            Atlantic Coastal Acquisition Corp. Class A Com...       $9.68   
ACAHU      

In [4]:
def func(tickers, start='2020-02-19', end='2020-03-23'):
    df = data.DataReader(tickers, 'yahoo', start=start, end=end).Close.T
    df1 = pd.DataFrame(columns=['max', 'min', 'discount'])
    df1['min'] = df.min(axis=1)
    df1['max'] = df.max(axis=1)
    df1['discount'] = 100 - df1['min'] / df1['max'] * 100
    return df1.join(all_tickers[['market_cap']]).sort_values(by='discount')

In [5]:
# companies with capitalization > 200 bil (optimization)
tickers = list(all_tickers[all_tickers.market_cap > 200].index)
df = func(tickers)
df


max          min   discount   market_cap
Symbols                                                  
VZ         58.220001    50.310001  13.586396   232.671801
WMT       122.580002   104.050003  15.116657   399.698095
LLY       143.199997   119.050003  16.864521   233.599418
BABA      222.139999   176.339996  20.617630   504.714875
PFE        34.535103    27.030361  21.730764   235.662912
TM        139.110001   108.500000  22.004170   249.258275
NFLX      386.190002   298.839996  22.618402   229.667432
AMZN     2170.219971  1676.609985  22.744698  1828.874553
PG        126.699997    97.699997  22.888714   344.833588
NVO        64.779999    49.459999  23.649274   205.626221
TSM        57.639999    43.889999  23.854962   588.818440
TMO       339.739990   255.300003  24.854297   208.414827
ADBE      383.279999   285.000000  25.641828   294.548592
JNJ       149.929993   111.139999  25.872070   454.682154
DHR       163.910004   121.389999  25.941067   207.459214
NVS        97.220001    70.669998  27.309198   204.259009
CMCSA      46.020000    33.369999  27.488052   269.041575
MSFT      187.279999   135.419998  27.691158  2158.097372
ORCL       55.509998    39.799999  28.301206   245.137600
PEP       145.850006   103.930000  28.741861   218.291236
CSCO       46.849998    33.200001  29.135535   233.380305
ABT        89.360001    62.820000  29.700090   212.880822
T          38.610001    26.770000  30.665631   201.343951
AAPL       80.904999    56.092499  30.668686  2544.601392
GOOG     1526.689941  1056.619995  30.790138  1833.521226
GOOGL    1524.869995  1054.130005  30.870828  1767.892086
PYPL      123.910004    85.260002  31.191994   352.982286
ABBV       94.959999    64.500000  32.076663   208.343587
FB        217.490005   146.009995  32.865883  1042.912321
ACN       215.919998   143.690002  33.452203   202.853968
INTC       67.110001    44.610001  33.527045   215.751260
CRM       193.360001   124.300003  35.715762   236.577048
UNH       305.309998   194.860001  36.176345   391.730750
V         213.309998   135.740005  36.364912   535.181836
KO         60.130001    37.560001  37.535339   247.084282
NVDA       78.675003    49.099998  37.591361   478.663360
ASML      317.390015   196.990005  37.934404   305.529605
HD        247.020004   152.149994  38.405801   347.961955
NKE       102.529999    62.799999  38.749634   260.317027
DIS       141.300003    85.760002  39.306440   326.139304
MA        344.559998   203.300003  40.997213   386.776102
JPM       137.490005    79.029999  42.519459   452.562890
XOM        60.340000    31.450001  47.878686   244.825556
BAC        34.849998    18.080000  48.120514   327.663052
TSLA      183.483994    72.244003  60.626536   621.136206

In [6]:
# companies with capitalization > 200 bil (optimization)
tickers = list(all_tickers[all_tickers.market_cap > 100].index)
df = func(tickers)
df


max          min   discount   market_cap
Symbols                                                  
VZ         58.220001    50.310001  13.586396   232.671801
COST      324.079987   279.850006  13.647859   187.587598
WMT       122.580002   104.050003  15.116657   399.698095
LLY       143.199997   119.050003  16.864521   233.599418
AMGN      222.960007   182.240005  18.263366   140.581869
UPS       106.760002    86.169998  19.286253   169.919260
MRK        79.169846    63.358780  19.971070   197.120744
BABA      222.139999   176.339996  20.617630   504.714875
JD         44.619999    35.240002  21.021958   100.975475
TGT       118.260002    92.620003  21.681041   127.816850
PFE        34.535103    27.030361  21.730764   235.662912
TM        139.110001   108.500000  22.004170   249.258275
NFLX      386.190002   298.839996  22.618402   229.667432
AMZN     2170.219971  1676.609985  22.744698  1828.874553
HSBC       36.459999    28.129999  22.846956   114.182001
PG        126.699997    97.699997  22.888714   344.833588
SONY       67.070000    51.680000  22.946175   123.461334
NVO        64.779999    49.459999  23.649274   205.626221
TSM        57.639999    43.889999  23.854962   588.818440
AZN        50.169998    37.790001  24.676097   178.024426
TMO       339.739990   255.300003  24.854297   208.414827
SNY        50.849998    38.020000  25.231069   129.261427
UL         59.950001    44.619999  25.571312   147.061719
ADBE      383.279999   285.000000  25.641828   294.548592
JNJ       149.929993   111.139999  25.872070   454.682154
DHR       163.910004   121.389999  25.941067   207.459214
MMM       159.339996   117.870003  26.026104   116.207448
TMUS      100.489998    74.320000  26.042391   180.569944
CVS        71.940002    52.299999  27.300532   110.117737
NVS        97.220001    70.669998  27.309198   204.259009
CMCSA      46.020000    33.369999  27.488052   269.041575
MSFT      187.279999   135.419998  27.691158  2158.097372
SE         52.560001    38.000000  27.701676   142.079524
ORCL       55.509998    39.799999  28.301206   245.137600
PEP       145.850006   103.930000  28.741861   218.291236
NOW       357.720001   254.699997  28.799062   114.971988
AMT       251.660004   179.089996  28.836528   130.443212
CSCO       46.849998    33.200001  29.135535   233.380305
BMY        65.709999    46.400002  29.386696   150.694625
ABT        89.360001    62.820000  29.700090   212.880822
TXN       133.130005    93.500000  29.767899   170.913862
T          38.610001    26.770000  30.665631   201.343951
AAPL       80.904999    56.092499  30.668686  2544.601392
GOOG     1526.689941  1056.619995  30.790138  1833.521226
GOOGL    1524.869995  1054.130005  30.870828  1767.892086
PYPL      123.910004    85.260002  31.191994   352.982286
CHTR      542.460022   371.700012  31.478819   148.910477
ABBV       94.959999    64.500000  32.076663   208.343587
EL        213.119995   144.380005  32.254125   119.549166
LIN       222.479996   150.000000  32.578208   155.410877
SAP       139.699997    94.129997  32.619900   166.816110
QCOM       90.559998    60.910000  32.740723   158.969040
FB        217.490005   146.009995  32.865883  1042.912321
CAT       137.210007    91.849998  33.058819   114.980523
PM         89.639999    59.980000  33.087907   155.604334
RIO        54.619999    36.419998  33.321130   134.020122
ACN       215.919998   143.690002  33.452203   202.853968
INTC       67.110001    44.610001  33.527045   215.751260
AMD        58.900002    38.709999  34.278441   110.603359
NEE        70.555000    45.415001  35.631776   152.718112
CRM       193.360001   124.300003  35.715762   236.577048
MDT       113.860001    72.919998  35.956440   175.003202
UNH       305.309998   194.860001  36.176345   391.730750
ZM        159.559998   101.760002  36.224615   109.145355
INTU      305.609985   194.720001  36.284804   142.890003
LMT       434.480011   276.799988  36.291663   104.150202
V         213.309998   135.740005  36.364912   535.181836
MCD       215.8

In [7]:
# companies with capitalization > 200 bil (optimization)
tickers = list(all_tickers[all_tickers.market_cap > 10].index)
df = func(tickers)
df


/home/comp/git/#my/best_in_crysis/cenv38/lib/python3.8/site-packages/pandas_datareader/base.py:272: SymbolWarning: Failed to read symbol: 'ABNB', replacing with NaN.
  warnings.warn(msg.format(sym), SymbolWarning)
/home/comp/git/#my/best_in_crysis/cenv38/lib/python3.8/site-packages/pandas_datareader/base.py:272: SymbolWarning: Failed to read symbol: 'AFRM', replacing with NaN.
  warnings.warn(msg.format(sym), SymbolWarning)
/home/comp/git/#my/best_in_crysis/cenv38/lib/python3.8/site-packages/pandas_datareader/base.py:272: SymbolWarning: Failed to read symbol: 'AGL', replacing with NaN.
  warnings.warn(msg.format(sym), SymbolWarning)
/home/comp/git/#my/best_in_crysis/cenv38/lib/python3.8/site-packages/pandas_datareader/base.py:272: SymbolWarning: Failed to read symbol: 'APP', replacing with NaN.
  warnings.warn(msg.format(sym), SymbolWarning)
/home/comp/git/#my/best_in_crysis/cenv38/lib/python3.8/site-packages/pandas_datareader/base.py:272: SymbolWarning: Failed to read symbol: 'ASAN', 

max           min   discount   market_cap
Symbols                                                    
CHT         36.820000     34.810001   5.458985    31.790016
CARR        12.750000     11.540000   9.490196    45.096013
OTIS        45.250000     40.000000  11.602210    37.859033
VZ          58.220001     50.310001  13.586396   232.671801
COST       324.079987    279.850006  13.647859   187.587598
LUMN        10.100000      8.690000  13.960403    14.125894
YUMC        46.049999     39.240002  14.788269    25.761670
WMT        122.580002    104.050003  15.116657   399.698095
PDD         37.689999     31.770000  15.707080    99.674058
ZTO         27.700001     23.330000  15.776176    21.505315
QGEN        41.570000     34.980000  15.852779    11.804074
TTWO       119.419998    100.150002  16.136323    19.458688
GILD        80.220001     67.000000  16.479682    86.450501
LLY        143.199997    119.050003  16.864521   233.599418
UMC          2.660000      2.210000  16.917294    22.931015
HRL         48.529999     40.080002  17.411904    25.851552
KEYS        98.599998     81.169998  17.677485    29.262456
KR          34.180000     28.129999  17.700413    29.911940
AMGN       222.960007    182.240005  18.263366   140.581869
PGR         81.459999     66.550003  18.303457    56.108976
GFL         17.750000     14.500000  18.309859    10.788797
DG         166.880005    136.100006  18.444390    54.362694
ZNGA         7.230000      5.870000  18.810514    11.040055
ATVI        64.370003     52.049999  19.139355    65.308259
CAG         29.879999     24.139999  19.210174    16.436760
REGN       494.429993    399.140015  19.272694    61.903016
UPS        106.760002     86.169998  19.286253   169.919260
VRTX       247.779999    199.770004  19.376057    52.510901
SJM        118.860001     95.790001  19.409389    14.303757
CHRW        74.820000     60.110001  19.660517    12.144525
CLX        197.880005    158.699997  19.799882    22.738939
MRK         79.169846     63.358780  19.971070   197.120744
SGEN       119.889999     95.750000  20.135123    26.208919
NLOK        20.790001     16.580000  20.250124    14.810714
CPB         53.840000     42.930000  20.263744    13.543371
SPOT       148.080002    117.639999  20.556457    45.248522
MASI       186.779999    148.380005  20.558943    14.784116
BABA       222.139999    176.339996  20.617630   504.714875
CL          76.269997     60.470001  20.715873    71.019079
GIS         59.669998     47.279999  20.764203    36.159380
JD          44.619999     35.240002  21.021958   100.975475
CTXS       130.500000    102.970001  21.095785    14.243202
CHD         76.610001     60.430000  21.119958    21.348656
BIIB       341.040009    268.880005  21.158809    49.771209
LOGI        43.040001     33.889999  21.259297    18.295513
TEAM       153.470001    120.570000  21.437415    66.258867
TGT        118.260002     92.620003  21.681041   127.816850
PFE         34.535103     27.030361  21.730764   235.662912
BIO        409.070007    320.010010  21.771334    20.917570
AOS         44.520000     34.750000  21.945194    11.249587
AKAM       102.559998     80.050003  21.948123    19.534553
TM         139.110001    108.500000  22.004170   249.258275
BDX        257.350006    200.580002  22.059453    74.068565
RGEN       109.139999     84.959999  22.155031    12.429273
EA         111.830002     86.940002  22.256996    40.554175
WBA         52.810001     41.020000  22.325318    40.498706
ABMD       168.080002    130.509995  22.352455    14.599262
ROL         27.146667     21.046667  22.470531    18.282389
TYL        336.570007    260.760010  22.524288    20.073995
NFLX       386.190002    298.839996  22.618402   229.667432
K           69.220001     53.560001  22.623519    21.693022
UI         146.750000    113.449997  22.691655    19.063459
AMZN      2170.219971   1676.609985  22.744698  1828.874553
SNP         54.599998     42.139999  22.820512    55.499042
HSBC        36.459999     28.129999  22.846956   114.18200